# Check implementation of Wajima-Hartmann model

In [1]:
import os

import numpy as np
import pandas as pd
import plotly.express as px
import plotly.figure_factory as ff
import plotly.graph_objects as go

from model import (
    define_wajima_model,
    define_hartmann_population_model)

## Define Wajima model

In [10]:
mechanistic_model, parameters_df = define_wajima_model()

## Reproduce Figure 2 in Wajima et al (2009)
Time course of coagulation factors and integral of fibrin during PT test
and aPPT test.

For details on the tests, see documentation.

### 1. Prothrombin test

In [11]:
# Prepare model for test
outputs = [
    'central.coagulation_factor_ii_concentration',
    'central.activated_coagulation_factor_ii_concentration',
    'central.coagulation_factor_x_concentration',
    'central.activated_coagulation_factor_x_concentration',
    'central.fibrinogen_concentration',
    'central.fibrin_concentration']
mechanistic_model.set_outputs(outputs)
parameters = np.array([
    parameters_df[parameters_df.Parameter == p].Value.values[0]
    for p in mechanistic_model.parameters()
])

# Dilute the plasma sample
n_states = mechanistic_model._n_states
parameters[:n_states] /= 3

# Set thrombomodulin concentration to zero
parameter_names = np.array(mechanistic_model.parameters())
index = np.where(parameter_names == 'central.thrombomodulin_amount')[0]
parameters[index] = 0

# Set endogenous production rates to zero
index = np.where(parameter_names == 'myokit.input_rate_vk')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_fibrinogen')[0]
parameters[index] = 0
index = np.where(
    parameter_names == 'myokit.production_rate_plasminogen')[0]
parameters[index] = 0
index = np.where(
    parameter_names == 'myokit.production_rate_prekrallikrein')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_tfpi')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_tmod')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_v')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_viii')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_xi')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_xii')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_xiii')[0]
parameters[index] = 0

# Make sure that only compounds in central compartment are considered
index = np.where(parameter_names == 'dose.drug_amount')[0]
parameters[index] = 0
index = np.where(
    parameter_names == 'peripheral_vitamin_k.vitamin_k_peripheral_amount'
)[0]
parameters[index] = 0
index = np.where(
    parameter_names == 'myokit.transition_rate_vk_central_to_peripheral'
)[0]
parameters[index] = 0
index = np.where(
    parameter_names == 'myokit.transition_rate_vk_peripheral_to_central'
)[0]
parameters[index] = 0

# Change time units to seconds (for numerical stability)
indices = []
for idp, name in enumerate(parameter_names):
    if 'rate' in name:
        indices.append(idp)
parameters[indices] /= 60 * 60

# Add 300 nM tissue factor
index = np.where(parameter_names == 'central.size')[0]
volume = parameters[index]
index = np.where(parameter_names == 'central.tissue_factor_amount')[0]
parameters[index] = 300 * volume

# Ensure excess of coagulation factor VII (set to 10 nM)
index = np.where(
    parameter_names == 'central.caogaulation_factor_vii_amount')[0]
parameters[index] = 10 * volume

# Integrate fibrin concentration curve
times = np.linspace(start=0, stop=90, num=1000)
delta_time = (times[1] - times[0])
simulation = mechanistic_model.simulate(parameters, times)
fibrin_auc = np.cumsum(simulation[-1] * delta_time)

Visualise results

In [12]:
# Figure 1: Change of coagulation factors
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[0] / simulation[0, 0],
    name='Prothrombin'
))
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[1] / simulation[0, 0],
    name='Thrombin'
))
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[2] / simulation[2, 0],
    name='Coag. factor X'
))
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[3] / simulation[2, 0],
    name='Act. coag. factor X'
))
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[4] / simulation[4, 0],
    name='Fibrinogen'
))
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[5] / simulation[4, 0],
    name='Fibrin'
))
fig.update_layout(
    xaxis_title='Time in seconds',
    yaxis_title=r'% of initial inactivated concentration',
    yaxis_range=[0, 1]
)
fig.show()

# Figure 2: Fibrin integral
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=times,
    y=fibrin_auc,
))
fig.add_shape(type="line",
    x0=0, y0=1500, x1=11.75, y1=1500,
    line=dict(
        color="red",
        width=2,
        dash="dash"
    )
)
fig.add_shape(type="line",
    x0=11.75, y0=-1, x1=11.75, y1=1500,
    line=dict(
        color="red",
        width=2,
        dash="dash",
    )
)
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title='Integral of fibrin in nMs',
    yaxis_type='log',
    yaxis_range=[-1, 6]
)
fig.show()

### 2. aPPT test (not relevant for this study, but useful as a implementation check)

In [13]:
# Prepare model for test
outputs = [
    'central.coagulation_factor_ii_concentration',
    'central.activated_coagulation_factor_ii_concentration',
    'central.coagulation_factor_x_concentration',
    'central.activated_coagulation_factor_x_concentration',
    'central.fibrinogen_concentration',
    'central.fibrin_concentration']
mechanistic_model.set_outputs(outputs)
parameters = np.array([
    parameters_df[parameters_df.Parameter == p].Value.values[0]
    for p in mechanistic_model.parameters()
])

# Dilute the plasma sample
n_states = mechanistic_model._n_states
parameters[:n_states] /= 3

# Set thrombomodulin concentration to zero
parameter_names = np.array(mechanistic_model.parameters())
index = np.where(parameter_names == 'central.thrombomodulin_amount')[0]
parameters[index] = 0

# Update coagulation factor (a)XI concentrations
index = np.where(parameter_names == 'central.size')[0]
volume = parameters[index]
index = np.where(
    parameter_names == 'central.coagulation_factor_xi_amount')[0]
initial_xi_conc = parameters[index]
parameters[index] = initial_xi_conc * 0.339
index = np.where(
    parameter_names == 'central.activated_coagulation_factor_xi_amount')[0]
parameters[index] = initial_xi_conc * 0.148

# Set endogenous production rates to zero
index = np.where(parameter_names == 'myokit.input_rate_vk')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_fibrinogen')[0]
parameters[index] = 0
index = np.where(
    parameter_names == 'myokit.production_rate_plasminogen')[0]
parameters[index] = 0
index = np.where(
    parameter_names == 'myokit.production_rate_prekrallikrein')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_tfpi')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_tmod')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_v')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_viii')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_xi')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_xii')[0]
parameters[index] = 0
index = np.where(parameter_names == 'myokit.production_rate_xiii')[0]
parameters[index] = 0

# Make sure that only compounds in central compartment are considered
index = np.where(parameter_names == 'dose.drug_amount')[0]
parameters[index] = 0
index = np.where(
    parameter_names == 'peripheral_vitamin_k.vitamin_k_peripheral_amount'
)[0]
parameters[index] = 0
index = np.where(
    parameter_names == 'myokit.transition_rate_vk_central_to_peripheral'
)[0]
parameters[index] = 0
index = np.where(
    parameter_names == 'myokit.transition_rate_vk_peripheral_to_central'
)[0]
parameters[index] = 0

# Change time units to seconds (for numerical stability)
indices = []
for idp, name in enumerate(parameter_names):
    if 'rate' in name:
        indices.append(idp)
parameters[indices] /= 60 * 60

# Add 300 nM contact activator
index = np.where(
    parameter_names == 'central.contact_system_activator_amount')[0]
parameters[index] = 300 * volume

# Integrate fibrin concentration curve
times = np.linspace(start=0, stop=90, num=1000)
delta_time = (times[1] - times[0])
simulation = mechanistic_model.simulate(parameters, times)
fibrin_auc = np.cumsum(simulation[-1] * delta_time)

Visualise results

In [14]:
# Visualise results
# Figure 1: Change of coagulation factors
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[0] / simulation[0, 0],
    name='Prothrombin'
))
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[1] / simulation[0, 0],
    name='Thrombin'
))
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[2] / simulation[2, 0],
    name='Coag. factor X'
))
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[3] / simulation[2, 0],
    name='Act. coag. factor X'
))
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[4] / simulation[4, 0],
    name='Fibrinogen'
))
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[5] / simulation[4, 0],
    name='Fibrin'
))
fig.update_layout(
    xaxis_title='Time in seconds',
    yaxis_title=r'% of initial inactivated concentration',
    yaxis_range=[0, 1]
)
fig.show()

# Figure 2: Fibrin integral
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=times,
    y=fibrin_auc,
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title='Integral of fibrin in nMs',
    yaxis_type='log',
    yaxis_range=[-1, 6]
)
fig.show()

## Reproduce Figure 3 in Wajima et al (2009)

Treatment response to daily 4 mg warfarin dose.

In [15]:
# Define outputs and dosing regimen
outputs_of_interest = [
    'central_warfarin.warfarin_concentration',
    'central.vitamin_k_concentration',
    'central.vitamin_k_hydroquinone_concentration',
    'central.vitamin_k_epoxide_concentration',
    'central.coagulation_factor_ii_concentration',
    'central.coagulation_factor_vii_concentration',
    'central.coagulation_factor_ix_concentration',
    'central.coagulation_factor_x_concentration']
n_states = mechanistic_model._n_states
plasma_sample_states = mechanistic_model.parameters()[:n_states]
mechanistic_model.set_outputs(outputs_of_interest + plasma_sample_states)
mechanistic_model.set_dosing_regimen(dose=4, start=0, period=24, num=20)

# Simulate treatment response over a period of 25 days
times = np.linspace(start=0, stop=24 * 20, num=1000)
parameters = np.array([
    parameters_df[parameters_df.Parameter == p].Value.values[0]
    for p in mechanistic_model.parameters()
])
simulation = mechanistic_model.simulate(parameters=parameters, times=times)

# Perform coagulation test for each plasma sample
inr_test_model, _ = define_wajima_model(patient=True, inr_test=True)
parameters = np.array([
    parameters_df[parameters_df.Parameter == p].Value.values[0]
    for p in inr_test_model.parameters()
])

prothrombin_time = np.empty(shape=len(times))
for ids, plasma_sample in enumerate(simulation[len(outputs_of_interest):].T):
    prothrombin_time[ids] = inr_test_model.compute_prothrombin_time(
        plasma_sample, parameters)

# Standardise PT to INR
prothrombin_time = prothrombin_time / prothrombin_time[0]

# Convert time unit to days
times /= 24

Visualise results

In [16]:
# Figure 1: Warfarin concentration
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[0],
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title='Warfarin concentration in mg/L',
    yaxis_range=[0, 1]
)
fig.show()

# Figure 2: Vitamin K related compounds
fig = go.Figure()
parameters = np.array([
    parameters_df[parameters_df.Parameter == p].Value.values[0]
    for p in mechanistic_model.parameters()
])
parameter_names = np.array(mechanistic_model.parameters())
index_amount = np.where(parameter_names == 'central.vitamin_k_amount')[0]
index_v = np.where(parameter_names == 'central.size')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[1] / initial_conc * 100,
    name='Vitamin K'
))
index_amount = np.where(
    parameter_names == 'central.vitamin_k_hydroquinone_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[2] / initial_conc * 100,
    name='Vitamin K hydroquinone'
))
index_amount = np.where(
    parameter_names == 'central.vitamin_k_epoxide_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[3] / initial_conc * 100,
    name='Vitamin K epoxide'
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title=r'Fraction of initial concentration in %',
    yaxis_range=[0, 150]
)
fig.show()

# Figure 3: Vitamin K dependent coagulation factors
fig = go.Figure()
index_amount = np.where(
    parameter_names == 'central.coagulation_factor_ii_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[4] / initial_conc * 100,
    name='II'
))
index_amount = np.where(
    parameter_names == 'central.coagulation_factor_vii_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[5] / initial_conc * 100,
    name='VII'
))
index_amount = np.where(
    parameter_names == 'central.coagulation_factor_ix_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[6] / initial_conc * 100,
    name='IX'
))
index_amount = np.where(
    parameter_names == 'central.coagulation_factor_x_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[7] / initial_conc * 100,
    name='X'
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title=r'Fraction of initial concentration in %',
    yaxis_range=[0, 150]
)
fig.show()

# Figure 4: Prothtombin time
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=times,
    y=prothrombin_time,
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title='Prothrombin time in INR',
    yaxis_range=[0, 2.5]
)
fig.show()

## Reproduce Figure 4 in Wajima et al (2009)

In [17]:
# Define outputs and dosing regimen
outputs_of_interest = [
    'central_warfarin.warfarin_concentration',
    'central.vitamin_k_concentration',
    'central.vitamin_k_hydroquinone_concentration',
    'central.vitamin_k_epoxide_concentration',
    'central.coagulation_factor_ii_concentration',
    'central.coagulation_factor_vii_concentration',
    'central.coagulation_factor_ix_concentration',
    'central.coagulation_factor_x_concentration']
n_states = mechanistic_model._n_states
plasma_sample_states = mechanistic_model.parameters()[:n_states]
mechanistic_model.set_outputs(outputs_of_interest + plasma_sample_states)
mechanistic_model.set_dosing_regimen(dose=50, start=0, period=24, num=20)

# Simulate treatment response over a period of 25 days
# 1. 0 - 20 days: Warfarin over dose (50mg)
times_1 = np.linspace(start=0, stop=24 * 20, num=1000)
parameters = np.array([
    parameters_df[parameters_df.Parameter == p].Value.values[0]
    for p in mechanistic_model.parameters()
])
simulation_1 = mechanistic_model.simulate(parameters=parameters, times=times_1)

# 2. 20 - 25 days: Single vitamin K dose (1 mg);
# molar mass of Vitamin K 450.7 ng/nmol
times_2 = np.linspace(start=0, stop=24 * 5, num=1000)
parameters[:n_states] = np.copy(simulation_1[-n_states:, -1])
index = np.where(parameter_names == 'central.vitamin_k_amount')[0]
parameters[index] = parameters[index] + 1E6 / 450.7
mechanistic_model.set_dosing_regimen(dose=0)
simulation_2 = mechanistic_model.simulate(parameters=parameters, times=times_2)
simulation = np.hstack((simulation_1, simulation_2))
times = np.hstack((times_1, times_2 + 24 * 20))

# Perform coagulation test for each plasma sample
prothrombin_time = np.empty(shape=len(times))
parameters = np.array([
    parameters_df[parameters_df.Parameter == p].Value.values[0]
    for p in mechanistic_model.parameters()
])
inr_test_model.set_test_duration(120)
for ids, plasma_sample in enumerate(simulation[len(outputs_of_interest):].T):
    prothrombin_time[ids] = inr_test_model.compute_prothrombin_time(
        plasma_sample, parameters)

# Standardise PT to INR
prothrombin_time = prothrombin_time / prothrombin_time[0]

# Convert time unit to days
times /= 24

Visualise results

In [18]:
# Figure 1: Warfarin concentration
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[0],
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title='Warfarin concentration in mg/L',
    yaxis_range=[0, 15]
)
fig.show()

# Figure 2: Vitamin K related compounds
fig = go.Figure()
parameters = np.array([
    parameters_df[parameters_df.Parameter == p].Value.values[0]
    for p in mechanistic_model.parameters()
])
parameter_names = np.array(mechanistic_model.parameters())
index_amount = np.where(parameter_names == 'central.vitamin_k_amount')[0]
index_v = np.where(parameter_names == 'central.size')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[1] / initial_conc * 100,
    name='Vitamin K'
))
index_amount = np.where(
    parameter_names == 'central.vitamin_k_hydroquinone_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[2] / initial_conc * 100,
    name='Vitamin K hydroquinone'
))
index_amount = np.where(
    parameter_names == 'central.vitamin_k_epoxide_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[3] / initial_conc * 100,
    name='Vitamin K epoxide'
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title=r'Fraction of initial concentration in %',
    yaxis_range=[0, 500]
)
fig.show()

# Figure 3: Vitamin K dependent coagulation factors
fig = go.Figure()
index_amount = np.where(
    parameter_names == 'central.coagulation_factor_ii_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[4] / initial_conc * 100,
    name='II'
))
index_amount = np.where(
    parameter_names == 'central.coagulation_factor_vii_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[5] / initial_conc * 100,
    name='VII'
))
index_amount = np.where(
    parameter_names == 'central.coagulation_factor_ix_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[6] / initial_conc * 100,
    name='IX'
))
index_amount = np.where(
    parameter_names == 'central.coagulation_factor_x_amount')[0]
initial_conc = parameters[index_amount] / parameters[index_v]
fig.add_trace(go.Scatter(
    x=times,
    y=simulation[7] / initial_conc * 100,
    name='X'
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title=r'Fraction of initial concentration in %',
    yaxis_range=[0, 150]
)
fig.show()

# Figure 4: Prothtombin time
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=times,
    y=prothrombin_time,
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title='Prothrombin time in INR',
    yaxis_range=[0, 9]
)
fig.show()

## Reproduce Figure 2 in Hartmann et al (2016)

In [19]:
# Define population model
mechanistic_model, _ = define_wajima_model()
population_model, pop_parameters_df = define_hartmann_population_model()

# Sample variation of parameters
seed = 12
n_patients = 100
parameters = np.array([
    pop_parameters_df[pop_parameters_df.Parameter == p].Value.values[0]
    for p in population_model.get_parameter_names()
])
patients = population_model.sample(
    parameters, n_samples=n_patients, seed=seed, covariates=[0, 0, 0, 71, 0])

# Define outputs and dosing regimen
outputs = [
    'central.coagulation_factor_ii_concentration',
    'central.coagulation_factor_v_concentration',
    'central.coagulation_factor_vii_concentration',
    'central.coagulation_factor_ix_concentration',
    'central.coagulation_factor_x_concentration',
    'central.coagulation_factor_xi_concentration',
    'central.coagulation_factor_xii_concentration',
    'central.coagulation_factor_xiii_concentration']
mechanistic_model.set_outputs(outputs)

# Simulate treatment response of patients over a period of 300 days
times = np.linspace(start=0, stop=300, num=1000) * 24
n_outputs = len(outputs)
n_times = len(times)
simulation = np.empty(shape=(n_patients, n_outputs, n_times))
for idp, p in enumerate(patients):
    # Simulate treatment response
    sim = mechanistic_model.simulate(parameters=p, times=times)
    simulation[idp] = sim

Visualise results

In [20]:
times /= 24  # Translate time to days
simulation /= simulation[..., :1]  # Normalise by init. conc.

fig = go.Figure()
upper = np.percentile(simulation[:, 0], 95, axis=0)
lower = np.percentile(simulation[:, 0], 5, axis=0)
fig.add_trace(go.Scatter(
    x=np.hstack((times, times[::-1])),
    y=np.hstack((upper, lower[::-1])),
    fill='toself',
    line_color='gray',
    name='5th to 95th percentile'
))
fig.add_trace(go.Scatter(
    x=times,
    y=np.median(simulation[:, 0], axis=0),
    name='median'
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title='Factor II concentration in %',
)
fig.show()

fig = go.Figure()
upper = np.percentile(simulation[:, 1], 95, axis=0)
lower = np.percentile(simulation[:, 1], 5, axis=0)
fig.add_trace(go.Scatter(
    x=np.hstack((times, times[::-1])),
    y=np.hstack((upper, lower[::-1])),
    fill='toself',
    line_color='gray',
    name='5th to 95th percentile'
))
fig.add_trace(go.Scatter(
    x=times,
    y=np.median(simulation[:, 1], axis=0),
    name='median'
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title='Factor V concentration in %',
)
fig.show()

fig = go.Figure()
upper = np.percentile(simulation[:, 2], 95, axis=0)
lower = np.percentile(simulation[:, 2], 5, axis=0)
fig.add_trace(go.Scatter(
    x=np.hstack((times, times[::-1])),
    y=np.hstack((upper, lower[::-1])),
    fill='toself',
    line_color='gray',
    name='5th to 95th percentile'
))
fig.add_trace(go.Scatter(
    x=times,
    y=np.median(simulation[:, 2], axis=0),
    name='median'
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title='Factor VII concentration in %',
)
fig.show()

fig = go.Figure()
upper = np.percentile(simulation[:, -1], 95, axis=0)
lower = np.percentile(simulation[:, -1], 5, axis=0)
fig.add_trace(go.Scatter(
    x=np.hstack((times, times[::-1])),
    y=np.hstack((upper, lower[::-1])),
    fill='toself',
    line_color='gray',
    name='5th to 95th percentile'
))
fig.add_trace(go.Scatter(
    x=times,
    y=np.median(simulation[:, -1], axis=0),
    name='median'
))
fig.update_layout(
    xaxis_title='Time in days',
    yaxis_title='Factor VIII concentration in %',
)
fig.show()

## Reproduce Figure 2 Hartmann et al (2020)

1. No covariates, just unexplained IIV

In [21]:
# Define population model
mechanistic_model, _ = define_wajima_model(inr_test=True)
population_model, pop_parameters_df = define_hartmann_population_model()

# Sample variation of parameters
seed = 12
n_patients = 1000
parameters = np.array([
    pop_parameters_df[pop_parameters_df.Parameter == p].Value.values[0]
    for p in population_model.get_parameter_names()
])
patients = population_model.sample(
    parameters, n_samples=n_patients, seed=seed, covariates=[0, 0, 0, 71, 0])

# Simulate treatment response of patients over a period of 300 days
inrs = []
times = [24 * 115]
mechanistic_model.set_dosing_regimen(dose=5, start=100 * 24, period=24)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

# Plot results
fig = ff.create_distplot(
    [inrs], ['5 mg'], show_hist=True, bin_size=.05, show_curve=False)
fig.update_layout(xaxis_title='INR')
fig.show()

2. With covariates and IIV on warfarin clearance and Vitamin K availability

We integrate Hamberg's covariate model into Hartmann et al's population model.
Hartmann et al orginally modify the clearance of Warfarin based on the CYP
genotype (-30% for *2/*2 and -80% for *3/*3), and the overall
Vitamin K availability based on the VKORC genotype (-44% for AA).

In agreement with this approach, Hamberg et al modify clearance of Warfarin
based on the CYP genotype (-50% for *2/*2 and -76% for *3/*3), and the EC50
of warfarin based on the VKORC genotype (-53% for AA). Importantly, Hamberg's
model assumes additivity of the effects of alleles, which also allows us to
describe *1/*2, *1/*3 and *2/*3 genotypes. Hamberg's model also has estimates
of the unexplained IIV of the clearance and the EC50. We therefore will use
Hamberg's model to extend Hartmann's model, making the simplifying assumption
that the effect of VKORC on the EC50 can be equated to the effect on the
Vitamin K availability.

In [22]:
# Define covariates
# Frequency of alleles matches dataset in publication
n_ids = 1000
n_cov = 5  # NOTE cov 1, 2 and 5 reference the VKORC genotype
covariates = np.zeros(shape=(n_ids, n_cov))

n_cyp2p9_33 = int(np.ceil(0.006 * n_ids))
covariates[:n_cyp2p9_33, 2] += 1
n_cyp2p9_23 = int(np.ceil(0.012 * n_ids))
covariates[:n_cyp2p9_33+n_cyp2p9_23, 2] += 1
n_cyp2p9_22 = int(np.ceil(0.014 * n_ids))
covariates[:n_cyp2p9_33+n_cyp2p9_23+n_cyp2p9_22, 2] += 1
n_cyp2p9_13 = int(np.ceil(0.123 * n_ids))
covariates[:n_cyp2p9_33+n_cyp2p9_23+n_cyp2p9_22+n_cyp2p9_13, 2] += 1
n_cyp2p9_12 = int(np.ceil(0.184 * n_ids))
covariates[
    :n_cyp2p9_33+n_cyp2p9_23+n_cyp2p9_22+n_cyp2p9_13+n_cyp2p9_12, 2] += 1

typical_age = 68
np.random.seed(12)
covariates[:, 3] = np.random.lognormal(
    mean=np.log(typical_age), sigma=0.1, size=n_ids)

n_vkorc1_AA = int(np.ceil(0.15 * n_ids))
covariates[:n_vkorc1_AA, [0, 1, 4]] += 1
n_vkorc1_GA = int(np.ceil(0.485 * n_ids))
covariates[:n_vkorc1_AA+n_vkorc1_GA, [0, 1, 4]] += 1

# Shuffle covariates
patient_cov = np.copy(covariates)
indices = np.random.choice(
    np.arange(n_ids), replace=False, size=n_ids)
patient_cov[:, 2] = covariates[indices, 2]

# Sample individual-level parameters
parameters = np.array([
    pop_parameters_df[pop_parameters_df.Parameter == p].Value.values[0]
    for p in population_model.get_parameter_names()
])
patients = population_model.sample(
    parameters, n_samples=n_ids, seed=seed, covariates=patient_cov)

# Simulate treatment response of patients over a period of 300 days
inrs = []
times = [115 * 24]
mechanistic_model.set_dosing_regimen(dose=2.5, start=24 * 100, period=24)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

mechanistic_model.set_dosing_regimen(dose=5, start=24 * 100, period=24)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

mechanistic_model.set_dosing_regimen(dose=7.5, start=24 * 100, period=24)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

# Plot results
df = pd.DataFrame({
    'INR': inrs,
    'Dose in mg':
        [2.5] * n_ids + [5] * n_ids + [7.5] * n_ids
})
fig = px.violin(df, y="INR", x="Dose in mg", box=True, points='all',
    hover_data=df.columns)
fig.show()

## Effect of VKORC1 genotype on INR

In [23]:
# Set up model
parameters = np.array([
    pop_parameters_df[pop_parameters_df.Parameter == p].Value.values[0]
    for p in population_model.get_parameter_names()
])
inrs = []
times = [115 * 24]
mechanistic_model.set_dosing_regimen(dose=5, start=24 * 100, period=24)

## Simulate for GG
cov = np.copy(patient_cov)
cov[:, [0, 1, 4]] = 0
patients = population_model.sample(
    parameters, n_samples=n_ids, seed=seed, covariates=cov)

# Simulate treatment response of patients over a period of 300 days
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

## Simulate for GA
cov = np.copy(patient_cov)
cov[:, [0, 1, 4]] = 1
patients = population_model.sample(
    parameters, n_samples=n_ids, seed=seed, covariates=cov)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

## Simulate for AA
cov = np.copy(patient_cov)
cov[:, [0, 1, 4]] = 2
patients = population_model.sample(
    parameters, n_samples=n_ids, seed=seed, covariates=cov)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

# Plot results
df = pd.DataFrame({
    'INR': inrs,
    'VKORC1':
        ['GG'] * n_ids + ['GA'] * n_ids + ['AA'] * n_ids
})
fig = px.violin(df, y="INR", x="VKORC1", box=True, points='all',
    hover_data=df.columns)
fig.show()

## Effect of CYP genotype on INR

In [24]:
# Set up model
parameters = np.array([
    pop_parameters_df[pop_parameters_df.Parameter == p].Value.values[0]
    for p in population_model.get_parameter_names()
])
inrs = []
times = [115 * 24]
mechanistic_model.set_dosing_regimen(dose=5, start=24 * 100, period=24)

## Simulate for *1/*1
cov = np.copy(patient_cov)
cov[:, 2] = 0
patients = population_model.sample(
    parameters, n_samples=n_ids, seed=seed, covariates=cov)

# Simulate treatment response of patients over a period of 300 days
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

## Simulate for *1/*2
cov = np.copy(patient_cov)
cov[:, 2] = 1
patients = population_model.sample(
    parameters, n_samples=n_ids, seed=seed, covariates=cov)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

## Simulate for *1/*3
cov = np.copy(patient_cov)
cov[:, 2] = 2
patients = population_model.sample(
    parameters, n_samples=n_ids, seed=seed, covariates=cov)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

## Simulate for *2/*2
cov = np.copy(patient_cov)
cov[:, 2] = 3
patients = population_model.sample(
    parameters, n_samples=n_ids, seed=seed, covariates=cov)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

## Simulate for *2/*3
cov = np.copy(patient_cov)
cov[:, 2] = 4
patients = population_model.sample(
    parameters, n_samples=n_ids, seed=seed, covariates=cov)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

## Simulate for *3/*3
cov = np.copy(patient_cov)
cov[:, 2] = 5
patients = population_model.sample(
    parameters, n_samples=n_ids, seed=seed, covariates=cov)
for idp, p in enumerate(patients):
    # Simulate treatment response
    inr = mechanistic_model.simulate(parameters=p, times=times)[0, 0]
    inrs.append(inr)

# Plot results
df = pd.DataFrame({
    'INR': inrs,
    'CYP2C9':
        ['*1/*1'] * n_ids + ['*1/*2'] * n_ids + ['*1/*3'] * n_ids \
        + ['*2/*2'] * n_ids + ['*2/*3'] * n_ids + ['*3/*3'] * n_ids
})
fig = px.violin(df, y="INR", x="CYP2C9", box=True, points='all',
    hover_data=df.columns)
fig.show()

## Find distribution of maintenance doses across patients

In [25]:
# Import distribution
directory = os.getcwd()
df = pd.read_csv(directory + '/maintenance_dose_distribution.csv')

# Round per pill
# mask = df['Maintenance dose'] < 1.5
# df['Maintenance dose'][mask] = 1
# mask = (df['Maintenance dose'] < 2.25) & (df['Maintenance dose'] > 1.5)
# df['Maintenance dose'][mask] = 2
# mask = df['Maintenance dose'] > 2
# df['Maintenance dose'][mask] = df['Maintenance dose'][mask].apply(
#     lambda x: np.round(2 * x) / 2)

# Plot results
fig = ff.create_distplot(
    [df['Maintenance dose'] * 7], ['INR = 2.5'], show_hist=False,
    bin_size=4, show_curve=True, show_rug=False)
fig.update_layout(xaxis_title='Weekly dose', xaxis_range=[0, 205])
fig.show()